In [1]:
# IMDB Review Datat Set Loading

from tensorflow.keras.datasets import imdb

(x_data_train, t_data_train), (x_data_test, t_data_test) = \
imdb.load_data(num_words=500)

In [5]:
# print(x_data_train.shape)  # (25000,)
# print(t_data_train.shape)  # (25000,)

from tensorflow.keras.preprocessing.sequence import pad_sequences

x_data_train_seq = pad_sequences(x_data_train, maxlen=100)

# print(x_data_train_seq.shape)  # (25000, 100)
# 모든 Review의 길이가 100개의 token으로 획일화!
# 각 Review에서 100개가 넘어가는 token은 삭제, 모자라는 token은 padding처리

# print(x_data_train_seq[0])
# [  2  33   6  22  12 215  28  77  52   5  14 407  16  82   2   8   4 107
#  117   2  15 256   4   2   7   2   5   2  36  71  43   2 476  26 400 317
#   46   7   4   2   2  13 104  88   4 381  15 297  98  32   2  56  26 141
#    6 194   2  18   4 226  22  21 134 476  26 480   5 144  30   2  18  51
#   36  28 224  92  25 104   4 226  65  16  38   2  88  12  16 283   5  16
#    2 113 103  32  15  16   2  19 178  32]

# 결국은 one-hot encoding으로 처리해야 해요!
# 하나하나의 token이 500개짜리 1차원 ndarray로 표현되어야 해요!
# 전체 데이터는 (100, 500)

from tensorflow.keras.utils import to_categorical

x_data_train_onehot = to_categorical(x_data_train_seq)

# print(x_data_train_onehot.shape)  # (25000, 100, 500)

(25000, 100, 500)


In [6]:
# RNN Model을 구현해 보아요!

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import SimpleRNN, Dense
from tensorflow.keras.optimizers import Adam

model = Sequential()

model.add(SimpleRNN(units=8,
                    activation='tanh',
                    input_shape=(100, 500)))

# output layer
model.add(Dense(units=1,
                activation='sigmoid'))

In [52]:
# 필요한 사항들에 대해 알아보았으니. . .
# 이제 전체 코드를 한 번 작성해 보아요!

# 필요한 module import

import numpy as np
import matplotlib.pyplot as plt
# 원래 의미는 train과 test로 분리하는거지만. . .
# 우리는 train과 validation 데이터를 분리하는 용도로 사용!
from sklearn.model_selection import train_test_split
from tensorflow.keras.datasets import imdb
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import SimpleRNN, Dense
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint

# 1. Data Loading
(x_data_train, t_data_train), (x_data_test, t_data_test) = \
imdb.load_data(num_words=500)

# 2. Data 확인
# print(x_data_train.shape)  # (25000,)

# 3. Data 분리(train data와 validation data)
x_data_train, x_data_valid, t_data_train, t_data_valid = \
train_test_split(x_data_train,
                 t_data_train,
                 test_size=0.2,
                 random_state=42,
                 stratify=t_data_train)

# review의 길이가 제각각인데 하나의 길이로 재단해야 해요!
x_data_train_seq = pad_sequences(x_data_train, maxlen=100)
x_data_valid_seq = pad_sequences(x_data_valid, maxlen=100)

# x_data를 one-hot형태로 변형해야 입력으로 사용이 가능!
x_data_train_onehot = to_categorical(x_data_train_seq)
x_data_valid_onehot = to_categorical(x_data_valid_seq)

# print(x_data_train_onehot.shape)  # (20000, 100, 500)
print(t_data_test.shape)

(25000,)


In [53]:
# Model 구현

model = Sequential()

model.add(SimpleRNN(units=8,
                    activation='tanh',
                    input_shape=(100,500)))

model.add(Dense(units=1,
                activation='sigmoid'))

model.compile(optimizer=Adam(learning_rate=1e-4),
              loss='binary_crossentropy',
              metrics=['acc'])

es_cb = EarlyStopping(monitor='val_loss',
                      patience=4,
                      verbose=1,
                      restore_best_weights=True)

cp_cb = ModelCheckpoint(filepath='./best-simplernn-model.ckpt',
                        monitor='val_loss',
                        verbose=1,
                        save_best_only=True)

history = model.fit(x_data_train_onehot,
                   t_data_train,
                   epochs=100,
                   batch_size=64,
                   validation_data=(x_data_valid_onehot,t_data_valid),
                   callbacks=[es_cb, cp_cb])

Epoch 1/100
313/313 [==============================] - 7s 19ms/step - loss: 0.6973 - acc: 0.5105 - val_loss: 0.6951 - val_acc: 0.5178

Epoch 00001: val_loss improved from inf to 0.69506, saving model to .\best-simplernn-model.ckpt
INFO:tensorflow:Assets written to: .\best-simplernn-model.ckpt\assets
Epoch 2/100
313/313 [==============================] - 5s 16ms/step - loss: 0.6911 - acc: 0.5293 - val_loss: 0.6902 - val_acc: 0.5362

Epoch 00002: val_loss improved from 0.69506 to 0.69021, saving model to .\best-simplernn-model.ckpt
INFO:tensorflow:Assets written to: .\best-simplernn-model.ckpt\assets
Epoch 3/100
313/313 [==============================] - 5s 15ms/step - loss: 0.6845 - acc: 0.5536 - val_loss: 0.6822 - val_acc: 0.5674

Epoch 00003: val_loss improved from 0.69021 to 0.68220, saving model to .\best-simplernn-model.ckpt
INFO:tensorflow:Assets written to: .\best-simplernn-model.ckpt\assets
Epoch 4/100
313/313 [==============================] - 4s 14ms/step - loss: 0.6643 - acc:

In [ ]:
train_loss = history.history['loss']
valid_loss = history.history['valid_loss']

plt.plot(train_loss, 'o', color='r')
plt.plot(valid_loss, color='b')

plt.show()

In [20]:
# 이번에는 one-hot이 아니라 word embedding방식으로 구현해 보아요!

# 필요한 module import 
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from tensorflow.keras.datasets import imdb
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import SimpleRNN, Dense, Embedding
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint

# 1. Data Loading
(x_data_train, t_data_train), (x_data_test, t_data_test) = \
imdb.load_data(num_words=500)

# 2. Data 확인
# print(x_data_train.shape)  # (25000,)

# 3. Data 분리(train data와 validation data)
x_data_train, x_data_valid, t_data_train, t_data_valid = \
train_test_split(x_data_train,
                 t_data_train,
                 test_size=0.2,
                 random_state=42,
                 stratify=t_data_train)

# review의 길이가 제각각인데 이거 하나의 길이로 재단해야 해요!
x_data_train_seq = pad_sequences(x_data_train, maxlen=100)
x_data_valid_seq = pad_sequences(x_data_valid, maxlen=100)

# Model 구현
model = Sequential()

model.add(Embedding(input_dim=500,
                    output_dim=16,
                    input_length=100))

model.add(SimpleRNN(units=8,
                    activation='tanh'))

model.add(Dense(units=1,
                activation='sigmoid'))

model.compile(optimizer=Adam(learning_rate=1e-4),
              loss='binary_crossentropy',
              metrics=['acc'])

es_cb = EarlyStopping(monitor='val_loss',
                      patience=4,
                      verbose=1,
                      restore_best_weights=True)

cp_cb = ModelCheckpoint(filepath='./best-simplernn-model.ckpt',
                        monitor='val_loss',
                        verbose=1,
                        save_best_only=True)

history = model.fit(x_data_train_seq,
                    t_data_train,
                    epochs=100,
                    batch_size=64,
                    validation_data=(x_data_valid_seq, t_data_valid),
                    callbacks=[es_cb, cp_cb])

Epoch 1/100
313/313 [==============================] - 5s 13ms/step - loss: 0.6878 - acc: 0.5433 - val_loss: 0.6692 - val_acc: 0.6150

Epoch 00001: val_loss improved from inf to 0.66922, saving model to .\best-simplernn-model.ckpt
INFO:tensorflow:Assets written to: .\best-simplernn-model.ckpt\assets
Epoch 2/100
313/313 [==============================] - 4s 12ms/step - loss: 0.6499 - acc: 0.6651 - val_loss: 0.6382 - val_acc: 0.6896

Epoch 00002: val_loss improved from 0.66922 to 0.63818, saving model to .\best-simplernn-model.ckpt
INFO:tensorflow:Assets written to: .\best-simplernn-model.ckpt\assets
Epoch 3/100
313/313 [==============================] - 4s 12ms/step - loss: 0.6179 - acc: 0.7189 - val_loss: 0.6140 - val_acc: 0.7090

Epoch 00003: val_loss improved from 0.63818 to 0.61396, saving model to .\best-simplernn-model.ckpt
INFO:tensorflow:Assets written to: .\best-simplernn-model.ckpt\assets
Epoch 4/100
313/313 [==============================] - 3s 11ms/step - loss: 0.5944 - acc:

In [23]:
from tensorflow.keras.preprocessing.text import Tokenizer

sentences = [
    '강감찬은 나를 너무 너무 좋아해',
    '강감찬은 영화를 좋아해'
]

tokenizer = Tokenizer()
tokenizer.fit_on_texts(sentences)

# 단어 인덱스를 확인해 보아요!
print(f'단어 인덱스는 : {tokenizer.word_index}')

# 숫자로 변형하려면 어떻게 해야 하나요?
word_encoding = tokenizer.texts_to_sequences(sentences)
print(word_encoding)

단어 인덱스는 : {'강감찬은': 1, '너무': 2, '좋아해': 3, '나를': 4, '영화를': 5}
[[1, 4, 2, 2, 3], [1, 5, 3]]


In [24]:
# 만약 단어사전에 없는 새로운 단어가 등장하면 어떻게 되나요?
new_sentence = [
    '강감찬은 신사임당을 너무 좋아해'
]

new_word_encoding = tokenizer.texts_to_sequences(new_sentence)
print(new_word_encoding)

# 기본적인 동작은 이렇게 단어사전에 없는 데이터는 변환이 안되기 때문에
# 그냥 없애버려요!

[[1, 2, 3]]


In [25]:
# 이렇게 처리하면 곤란해요! OOV(out of vocabulary) token은 따로 처리해줘야 해요!

from tensorflow.keras.preprocessing.text import Tokenizer

sentences = [
    '강감찬은 나를 너무 너무 좋아해',
    '강감찬은 영화를 좋아해'
]

tokenizer = Tokenizer(oov_token='<OOV>')
tokenizer.fit_on_texts(sentences)

# 단어 인덱스를 확인해보아요!
print(f'단어 인덱스는 : {tokenizer.word_index}')

# 숫자로 변형하려면 어떻게 해야 하나요?
word_encoding = tokenizer.texts_to_sequences(sentences)
print(word_encoding)

# 만약 단어사전에 없는 새로운 단어가 등장하면 어떻게 되나요?
new_sentence = [
    '강감찬은 신사임당을 너무 좋아해'
]

new_word_encoding = tokenizer.texts_to_sequences(new_sentence)
print(new_word_encoding)

# 기본적인 동작은 이렇게 단어사전에 없는 데이터는 변환이 안되기 때문에
# 그냥 없애버려요!

단어 인덱스는 : {'<OOV>': 1, '강감찬은': 2, '너무': 3, '좋아해': 4, '나를': 5, '영화를': 6}
[[2, 5, 3, 3, 4], [2, 6, 4]]
[[2, 1, 3, 4]]


In [26]:
# 위처럼 vocabulary를 구성하면 모든 token들이 포함되는 단어사전이 만들어져요!
# 이렇게 하면 단어사전이 너무 커지는 문제가 발생해요!
# 일반적으로 빈도수가 높은 단어들만 단어사전에 포함시켜요!
# 빈도수가 높은 순서로 최대 사전개수를 정하고 빈도수가 적은 단어를 제외하면 되요!

from tensorflow.keras.preprocessing.text import Tokenizer

sentences = [
    '강감찬은 나를 너무 너무 좋아해',
    '강감찬은 영화를 좋아해'
]

tokenizer = Tokenizer(oov_token='<OOV>')
tokenizer.fit_on_texts(sentences)

# 단어 인덱스를 확인해보아요!
print(f'단어 인덱스는 : {tokenizer.word_index}')

# 숫자로 변형하려면 어떻게 해야 하나요?
word_encoding = tokenizer.texts_to_sequences(sentences)
print(word_encoding)

# 만약 단어사전에 없는 새로운 단어가 등장하면 어떻게 되나요?
new_sentence = [
    '강감찬은 신사임당을 너무 좋아해'
]
new_word_encoding = tokenizer.texts_to_sequences(new_sentence)
print(new_word_encoding)

# 이제 길이도 맞춰야 해요!
from tensorflow.keras.preprocessing.sequence import pad_sequences

padding = pad_sequences(word_encoding, maxlen=4)
print(padding)

단어 인덱스는 : {'<OOV>': 1, '강감찬은': 2, '너무': 3, '좋아해': 4, '나를': 5, '영화를': 6}
[[2, 5, 3, 3, 4], [2, 6, 4]]
[[2, 1, 3, 4]]
[[5 3 3 4]
 [0 2 6 4]]


In [29]:
# 기본적인 내용을 알아봤으니 이제 실제로 구현 해 보아요!
# 필요한 module import
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import tensorflow as tf

# Naver가 제공하는 네이버 영화 리뷰 데이터를 로딩해 보아요!
train_file = tf.keras.utils.get_file(
    r"C:\Users\lee_0\Documents\my_ws\edu\machine_learning\ratings_train.txt",
    origin=r'https://raw.githubusercontent.com/e9t/nsmc/master/ratings_train.txt',
    extract=True
)

train_df = pd.read_csv(train_file, sep='\t')
display(train_df.head(), train_df.shape)  # (150000, 3)

test_file = tf.keras.utils.get_file(
    r"C:\Users\lee_0\Documents\my_ws\edu\machine_learning\ratings_test.txt",
    origin=r'https://raw.githubusercontent.com/e9t/nsmc/master/ratings_test.txt',
    extract=True
)

test_df = pd.read_csv(test_file, sep='\t')
display(test_df.head(), test_df.shape)  # (50000, 3)

id                                           document  label
0   9976970                                아 더빙.. 진짜 짜증나네요 목소리      0
1   3819312                  흠...포스터보고 초딩영화줄....오버연기조차 가볍지 않구나      1
2  10265843                                  너무재밓었다그래서보는것을추천한다      0
3   9045019                      교도소 이야기구먼 ..솔직히 재미는 없다..평점 조정      0
4   6483659  사이몬페그의 익살스런 연기가 돋보였던 영화!스파이더맨에서 늙어보이기만 했던 커스틴 ...      1

(150000, 3)

4907008/4893335 [==============================] - 0s 0us/step


id                                           document  label
0  6270596                                                굳 ㅋ      1
1  9274899                               GDNTOPCLASSINTHECLUB      0
2  8544678             뭐야 이 평점들은.... 나쁘진 않지만 10점 짜리는 더더욱 아니잖아      0
3  6825595                   지루하지는 않은데 완전 막장임... 돈주고 보기에는....      0
4  6723715  3D만 아니었어도 별 다섯 개 줬을텐데.. 왜 3D로 나와서 제 심기를 불편하게 하죠??      0

(50000, 3)

In [32]:
# 간단하게 데이터 확인과정만 해 보아요!

# 긍정과 부정 댓글의 비율부터 알아보아요!
cnt = train_df['label'].value_counts()
# print(cnt)
# 0    75173
# 1    74827
# 긍정과 부정 댓글 비율이 5:5예요. 다행이죠!

# 결측치 확인
train_df.isnull().sum()
# id          0
# document    5
# label       0
# 댓글중에는 5개가 결측치예요. 나중에 당연히 삭제하고 학습에 이용해야 해요!

id          0
document    5
label       0
dtype: int64

In [33]:
# 형태소 분석해야 해요!
# 다양한 한국어 형태소 분석기가 있어요!
# Kkma, Komoran, Okt, Mecab 등등이 있어요!
# 어떤 형태소 분석기를 사용하느냐에 따라 결과가 달라져요!
# 이런거 어떻게 사용하나요? koNLPy라는 라이브러리를 이용해요!
# Colab같은 경우 간단히 해당 라이브러리만 설치하면 되요!

In [34]:
from konlpy.tag import Okt, Komoran, Kkma

kkma = Kkma()
okt = Okt()
komoran = Komoran()

text = '이것은 소리없는 아우성. 저 푸른 해원을 향하여 흔드는 노스텔지어의 손수건'

print(kkma.morphs(text))
# ['이것', '은', '소리', '없', '는', '아우성', '.', '저', '푸른', '해원', '을', '향하', '여', '흔들', '는', '노스텔지어', '의', '손수건']

print(okt.morphs(text))
# ['이', '것', '은', '소리', '없는', '아우성', '.', '저', '푸른', '해원', '을', '향', '하여', '흔드는', '노스', '텔', '지', '어의', '손수건']

print(komoran.morphs(text))
# ['이것', '은', '소리', '없', '는', '아우성', '.', '저', '푸른', '해원', '을', '향하', '아', '흔들', '는', '노스', '텔', '짓', '어', '의', '손수건']

['이것', '은', '소리', '없', '는', '아우성', '.', '저', '푸른', '해원', '을', '향하', '여', '흔들', '는', '노스텔지어', '의', '손수건']
['이', '것', '은', '소리', '없는', '아우성', '.', '저', '푸른', '해원', '을', '향', '하여', '흔드는', '노스', '텔', '지', '어의', '손수건']
['이것', '은', '소리', '없', '는', '아우성', '.', '저', '푸른', '해원', '을', '향하', '아', '흔들', '는', '노스', '텔', '짓', '어', '의', '손수건']


In [38]:
# 데이터 전처리도 진행해야 해요!

# 1. 댓글데이터에는 특수문자, 숫자 이렇게 함께 포함되어 있어요!
#    정규식을 사용해서 영어, 한글, 띄어쓰기만 남기고 나머지 특수문자는 제거!

# 2. 결츨치 제거(5)

# 3. stopword(불용어)를 제거해야 해요!

# 4. 단어사전을 만들고 숫자로 변경하는 token화 작업을 진행하면 되요!

# 5. 동일한 문장 길이로 정리하면 되죠! (padding 처리)

##############################################
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import tensorflow as tf

# Naver가 제공하는 네이버 영화 리뷰 데이터를 로딩해 보아요!
train_file = tf.keras.utils.get_file(
    r'C:\Users\lee_0\Documents\my_ws\edu\machine_learning\ratings_train.txt',
    origin=r'https://raw.githubusercontent.com/e9t/nsmc/master/ratings_train.txt',
    extract=True
)

train_df = pd.read_csv(train_file, sep='\t')

test_file = tf.keras.utils.get_file(
    r'C:\Users\lee_0\Documents\my_ws\edu\machine_learning\ratings_test.txt',
    origin=r'https://raw.githubusercontent.com/e9t/nsmc/master/ratings_test.txt',
    extract=True
)

test_df = pd.read_csv(test_file, sep='\t')

# 데이터를 다운로드 해서 DataFrame으로 생성해 보아요!

# 1. 특수문자 제거(정규식을 이용해요!)
train_df['document'] = train_df['document'].str.replace('[^A-Za-z가-힣ㄱ-ㅎㅏ-ㅣ]', '')
# display(train_df.head())

# 2. 결측치 제거(5개)
train_df = train_df.dropna()
# print(train_df.shape)  # (149995, 3)

# 3. stopword(불용어) 처리
#    관사, 전치사, 조사, 접속사등의 의미가 없는 단어를 불용어라 하는데
#    당연히 처리해야 해요! 한글에는 이런 불용어가 정말 어마어마하게 많아요!
#    그걸 다 처리하기는 불가능하구요. 자주 사용하는거 몇개만 처리하도록 할께요!
from konlpy.tag import Okt, Kkma, Komoran

okt = Okt()

def word_tokenization(text):
    stop_words = ['는', '을', '를', '이', '가', '의', '던', '고', '하', '다', '은', '에', '들', '지', '게', '도']
    return [word for word in okt.morphs(text) if word not in stop_words]

data_train = train_df['document'].apply(lambda x:word_tokenization(x))

display(data_train.head())

0                              [아더, 빙, 진짜, 짜증나네요, 목소리]
1        [흠, 포스터, 보고, 초딩, 영화, 줄, 오버, 연기, 조차, 가볍지, 않구나]
2                     [너, 무재, 밓었, 다그, 래서, 보는것을, 추천, 한]
3                  [교도소, 이야기, 구먼, 솔직히, 재미, 없다, 평점, 조정]
4    [사이, 몬페, 그, 익살스런, 연기, 돋보였던, 영화, 스파이더맨, 에서, 늙어,...
Name: document, dtype: object

In [39]:
# 불용어 처리가 됬다고 가정하고 진행해야 될꺼 같아요!

# 단어사전을 만들고 문자를 숫자로 변경하는 token화 진행!
from tensorflow.keras.preprocessing.text import Tokenizer

tokenizer = Tokenizer()
tokenizer.fit_on_texts(data_train)  # 단어사전 생성!
# 일단 총 단어개수가 몇개인지 알아보아요!
print(f'총 단어개수는 : {len(tokenizer.word_index)}')

# 단어사전을 출력해 보아요!
print(tokenizer.word_index)

# 각 토큰이 나타난 수(빈도)를 알아보아요!
print(tokenizer.word_counts)

# 단어 빈도수가 5회 이상인 단어가 몇개인지 확인!
def get_voca_size(threshold):
    count = 0
    for x in tokenizer.word_counts.values():
        if x > threshold:
            count += 1
    return count

voca_size = get_voca_size(5)
print(voca_size)

총 단어개수는 : 122402
{'영화': 1, '한': 2, '너무': 3, '정말': 4, '적': 5, '만': 6, '진짜': 7, '로': 8, '으로': 9, '에서': 10, '내': 11, '평점': 12, '과': 13, '최고': 14, '그': 15, '인': 16, '나': 17, '이런': 18, '연기': 19, '와': 20, '생각': 21, '스토리': 22, '점': 23, '이다': 24, '이영화': 25, '드라마': 26, '감동': 27, '사람': 28, '요': 29, 'ㅋㅋ': 30, '하고': 31, '보고': 32, '배우': 33, '왜': 34, '감독': 35, '네': 36, '때': 37, '그냥': 38, '아': 39, '시간': 40, '까지': 41, '쓰레기': 42, '못': 43, '보다': 44, '중': 45, '것': 46, '뭐': 47, '재미': 48, '본': 49, '말': 50, '면': 51, '없는': 52, '잘': 53, '작품': 54, '더': 55, '봤는데': 56, '좀': 57, '거': 58, '사랑': 59, '마지막': 60, '저': 61, '대': 62, '없다': 63, '정도': 64, '좋은': 65, '화': 66, 'ㅠㅠ': 67, '이나': 68, '완전': 69, 'ㅋㅋㅋ': 70, 'ㅋ': 71, '처음': 72, '같은': 73, '라': 74, '입니다': 75, '개': 76, '액션': 77, '이렇게': 78, '최악': 79, '주인공': 80, '니': 81, '내용': 82, '느낌': 83, 'ㅡㅡ': 84, '서': 85, '안': 86, '이야기': 87, '성': 88, '기': 89, '인데': 90, '연출': 91, '봐도': 92, '명작': 93, '돈': 94, '장면': 95, '끝': 96, '역시': 97, '임': 98, '없고': 99, '많이': 100, '볼': 101, '그리고': 102

In [42]:
# 단어사전을 생성합니다.
tokenizer = Tokenizer(oov_token='<OOV>',
                      num_words=15000)
tokenizer.fit_on_texts(data_train)

print(tokenizer.word_index)

# 이제 각 문장을 숫자 벡터로 변환하여 encoding
data_train_seq = tokenizer.texts_to_sequences(data_train)
print(data_train_seq[0])
print(data_train_seq[1])

{'<OOV>': 1, '영화': 2, '한': 3, '너무': 4, '정말': 5, '적': 6, '만': 7, '진짜': 8, '로': 9, '으로': 10, '에서': 11, '내': 12, '평점': 13, '과': 14, '최고': 15, '그': 16, '인': 17, '나': 18, '이런': 19, '연기': 20, '와': 21, '생각': 22, '스토리': 23, '점': 24, '이다': 25, '이영화': 26, '드라마': 27, '감동': 28, '사람': 29, '요': 30, 'ㅋㅋ': 31, '하고': 32, '보고': 33, '배우': 34, '왜': 35, '감독': 36, '네': 37, '때': 38, '그냥': 39, '아': 40, '시간': 41, '까지': 42, '쓰레기': 43, '못': 44, '보다': 45, '중': 46, '것': 47, '뭐': 48, '재미': 49, '본': 50, '말': 51, '면': 52, '없는': 53, '잘': 54, '작품': 55, '더': 56, '봤는데': 57, '좀': 58, '거': 59, '사랑': 60, '마지막': 61, '저': 62, '대': 63, '없다': 64, '정도': 65, '좋은': 66, '화': 67, 'ㅠㅠ': 68, '이나': 69, '완전': 70, 'ㅋㅋㅋ': 71, 'ㅋ': 72, '처음': 73, '같은': 74, '라': 75, '입니다': 76, '개': 77, '액션': 78, '이렇게': 79, '최악': 80, '주인공': 81, '니': 82, '내용': 83, '느낌': 84, 'ㅡㅡ': 85, '서': 86, '안': 87, '이야기': 88, '성': 89, '기': 90, '인데': 91, '연출': 92, '봐도': 93, '명작': 94, '돈': 95, '장면': 96, '끝': 97, '역시': 98, '임': 99, '없고': 100, '많이': 101, '볼': 102, '그리고': 103, '

In [43]:
# 동일한 길이로 문장 길이를 정리해야 해요!
max_length = max([len(x) for x in data_train_seq])
print(max_length)

from tensorflow.keras.preprocessing.sequence import pad_sequences

x_data_train = pad_sequences(data_train_seq,
                             maxlen=max_length)

t_data_train = train_df['label'].values
print(x_data_train[:1])  # padding 처리

69
[[    0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0 13657     1     8  6835   615]]


In [44]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Embedding, Bidirectional
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint

model = Sequential()

model.add(Embedding(input_dim=15000,
                    output_dim=32,
                    input_length=71))

# 양방향 LSTM을 만들어요! (조금 더 학습이 잘 되게 하기 위해서!)
model.add(Bidirectional(LSTM(units=16,
                             activation='tanh')))

# hidden layer
model.add(Dense(units=32,
                activation='relu'))

# output layer
model.add(Dense(units=1,
                activation='sigmoid'))

model.compile(optimizer=Adam(learning_rate=1e-4),
              loss='binary_crossentropy',
              metrics=['acc'])

# Callback 설정
cp_cb = ModelCheckpoint(filepath='./best_model.chpt',
                        save_weights_only=True,
                        save_best_only=True,
                        monitor='val_loss',
                        verbose=1)

es_cb = EarlyStopping(monitor='val_loss',
                      patience=3,
                      verbose=1)

# 학습 진행
history = model.fit(x_data_train,
                    t_data_train,
                    epochs=10,
                    batch_size=64,
                    validation_split=0.2,
                    callbacks=[cp_cb, es_cb],
                    verbose=1)

Epoch 1/10
1875/1875 [==============================] - 32s 16ms/step - loss: 0.5188 - acc: 0.7324 - val_loss: 0.3868 - val_acc: 0.8283

Epoch 00001: val_loss improved from inf to 0.38680, saving model to .\best_model.chpt
Epoch 2/10
1875/1875 [==============================] - 30s 16ms/step - loss: 0.3515 - acc: 0.8458 - val_loss: 0.3580 - val_acc: 0.8432

Epoch 00002: val_loss improved from 0.38680 to 0.35800, saving model to .\best_model.chpt
Epoch 3/10
1875/1875 [==============================] - 31s 17ms/step - loss: 0.3190 - acc: 0.8617 - val_loss: 0.3531 - val_acc: 0.8457

Epoch 00003: val_loss improved from 0.35800 to 0.35305, saving model to .\best_model.chpt
Epoch 4/10
1875/1875 [==============================] - 30s 16ms/step - loss: 0.3014 - acc: 0.8704 - val_loss: 0.3566 - val_acc: 0.8438

Epoch 00004: val_loss did not improve from 0.35305
Epoch 5/10
1875/1875 [==============================] - 30s 16ms/step - loss: 0.2892 - acc: 0.8765 - val_loss: 0.3594 - val_acc: 0.8430

In [46]:
# 학습이 끝난 다음. . . prediction을 할 수 있어요!
# 예측 데이터는 다음과 같은 데이터를 사용해 보세요!

review_sentences = ['내가 만들어도 이것보단 잘 만들겠다.',
                    '너무너무 재미있었습니다. 감사합니다.',
                    '아..내 돈... 돈 아까워 죽을거 같아요',
                    '아나..이것도 영화라고 만들었냐. 무슨 스토리가 산으로 가냐',
                    '감동과 재미가 같이 있는 영화입니다. 훌륭합니다.',
                    '너무너무 재미없다.. 잠와 죽는줄.',
                    '너무너무 재미있다.. 잠이 확깨네.']

df = pd.DataFrame({'document' : review_sentences})

# 정규식을 활용해 영어, 한글, 띄어쓰기만 남기고 나머지 특수문자를 제거
df['document'] = df['document'].str.replace('[^A-Za-z가-힣ㄱ-ㅎㅏ-ㅣ ]', '')

# 불용어(stopword)제거

okt = Okt()

def word_tokenization(text):
    stop_words = ['는', '을', '를', '이', '가', '의', '던', '고', '하', '다', '은', '에', '들', '지', '게', '도']
    return [word for word in okt.morphs(text) if word not in stop_words]

data_predict = df['document'].apply((lambda x:word_tokenization(x)))

# 4. 각 문장을 숫자 벡터로 변환하여 encoding
data_predict_seq = tokenizer.texts_to_sequences(data_predict)

# 5. 동일한 문장 길이로 정리해야 합니다.
x_data_predict = pad_sequences(data_predict_seq,
                               truncating='post',
                               padding='pre',
                               maxlen=max_length)

# predict
print(model.predict(x_data_predict))

[[0.01703128]
 [0.9896993 ]
 [0.01438022]
 [0.01217189]
 [0.99416244]
 [0.01100361]
 [0.53533596]]
